In [19]:
import numpy as np
from collections import defaultdict

def levenshtein_distance(hypothesis: list, reference: list):
    """编辑距离
    计算两个序列的levenshtein distance，可用于计算 WER/CER
    参考资料：
        https://www.cuelogic.com/blog/the-levenshtein-algorithm
        https://martin-thoma.com/word-error-rate-calculation/

    C: correct
    W: wrong
    I: insert
    D: delete
    S: substitution

    :param hypothesis: 预测序列
    :param reference: 真实序列
    :return: 1: 错误操作，所需要的 S，D，I 操作的次数；
             2: ref 与 hyp 的所有对齐下标；
             3: 返回 C、W、S、D、I 各自的数量；
    """
    len_hyp = len(hypothesis)
    len_ref = len(reference)
    cost_matrix = np.zeros((len_hyp + 1, len_ref + 1), dtype=np.int16)

    # 记录所有的操作，0-equal；1-insertion；2-deletion；3-substitution
    ops_matrix = np.zeros((len_hyp + 1, len_ref + 1), dtype=np.int8)

    for i in range(len_hyp + 1):
        cost_matrix[i][0] = i
        pass
    
    for j in range(len_ref + 1):
        cost_matrix[0][j] = j
        pass

    # 生成 cost 矩阵和 operation矩阵，i:外层hyp，j:内层ref
    for i in range(1, len_hyp + 1):
        for j in range(1, len_ref + 1):
            if hypothesis[i-1] == reference[j-1]:
                cost_matrix[i][j] = cost_matrix[i-1][j-1]
                pass
            else:
                substitution = cost_matrix[i-1][j-1] + 1
                insertion = cost_matrix[i-1][j] + 1
                deletion = cost_matrix[i][j-1] + 1

                # compare_val = [insertion, deletion, substitution]   # 优先级
                compare_val = [substitution, insertion, deletion]   # 优先级

                min_val = min(compare_val)
                operation_idx = compare_val.index(min_val) + 1
                cost_matrix[i][j] = min_val
                ops_matrix[i][j] = operation_idx
                pass
            pass
        pass
    

    match_idx = []  # 保存 hyp与ref 中所有对齐的元素下标
    i = len_hyp
    j = len_ref
    nb_map = {"N": len_ref, "C": 0, "W": 0, "I": 0, "D": 0, "S": 0}
    while i >= 0 or j >= 0:
        i_idx = max(0, i)
        j_idx = max(0, j)

        if ops_matrix[i_idx][j_idx] == 0:     # correct
            if i-1 >= 0 and j-1 >= 0:
                match_idx.append((j-1, i-1))
                nb_map['C'] += 1
                pass

            # 出边界后，这里仍然使用，应为第一行与第一列必然是全零的
            i -= 1
            j -= 1
            pass
        elif ops_matrix[i_idx][j_idx] == 2: # insert
            i -= 1
            nb_map['I'] += 1
            pass
        elif ops_matrix[i_idx][j_idx] == 3: # delete
            j -= 1
            nb_map['D'] += 1
            pass
        elif ops_matrix[i_idx][j_idx] == 1: # substitute
            i -= 1
            j -= 1
            nb_map['S'] += 1
            pass

        # 出边界处理
        if i < 0 and j >= 0:
            nb_map['D'] += 1
            pass
        elif j < 0 and i >= 0:
            nb_map['I'] += 1
            pass
        pass

    match_idx.reverse()
    wrong_cnt = cost_matrix[len_hyp][len_ref]
    nb_map["W"] = wrong_cnt

    print("ref: %s" % " ".join(reference))
    print("hyp: %s" % " ".join(hypothesis))
    print(nb_map)
#     print("match_idx: %s" % str(match_idx))
    return wrong_cnt, match_idx, nb_map


def test():
    """
    id: (301225575230191207_spkb_f-301225575230191207_spkb_f_slice19)
    Scores: (#C #S #D #I) 27 4 1 2
    Eval:
    :return:
    """
    
    mic = 'ihm'
    dataset = 'dev'
    
    total_wrong = 0
    total_words = 0
    
    nbest = load_nbest('./../../ami_nbest/' + mic + '_' + dataset + '_text')
    text = load_nbest('./../../ami_nbest/' + mic + '_' + dataset + '_ref')
    
    nbest_and_wer = defaultdict()
    
    for key in nbest.keys():
        print("key:", key)
        for sent in nbest[key]:
            ref = text[key][0].split(' ')
            hyp = sent.split(' ')
            wrong_cnt, match_idx, nb_map = levenshtein_distance(reference=ref, hypothesis=hyp)
            words = nb_map['N']
            wrong = nb_map['W']
            wer = nb_map['W'] / nb_map['N']
            
            if key in nbest_and_wer:
                nbest_and_wer[key].append((sent, wer, words, wrong))
                wer_list.append(wer)
                pass
            else:
                nbest_and_wer[key] = [(sent, wer, words, wrong)]
                wer_list = [wer]
                pass
            pass
            
        min_id = wer_list.index(max(wer_list))

        best_hyp, best_wer, ref_len, num_wrong = nbest_and_wer[key][min_id]
        
        total_wrong += num_wrong
        total_words += ref_len
        
        print(total_wrong / total_words)
        
        with open('./../../ami_nbest/' + mic + '_' + dataset + '_best', "a") as f:
            f.write(key + ' ' + best_hyp + '\n')
            pass
        pass

    
def load_nbest(path):
    r"""Read nbest lists.

    Assume the input file format is as following:
        en_4156-A_030185-030248-1 oh yeah
        en_4156-A_030470-030672-1 well i'm going to have mine and two more classes
        en_4156-A_030470-030672-2 well i'm gonna have mine and two more classes
        ...

    Args:
        path (str): A file of nbest lists with the above format.

    Returns:
        The nbest lists represented by a dictionary from string to a list of
        strings. The key is utterance id and the value is the hypotheses.
    """

    nbest = defaultdict()
    with open(path, 'r', encoding='utf-8') as f:
        for line in f:
            line = line.strip()
            try:
                key, hyp = line.split(' ', 1)
            except ValueError:
                key = line
                hyp = ' '
            key = key.rsplit('-', 1)[0]
            if key not in nbest:
                nbest[key] = [hyp]
            else:
                nbest[key].append(hyp)
    return nbest


if __name__ == '__main__':
    test()

key: AMI_ES2011a_H00_FEE041_0003427_0003714
ref: HERE WE GO
hyp: HERE WE GO
{'N': 3, 'C': 3, 'W': 0, 'I': 0, 'D': 0, 'S': 0}
ref: HERE WE GO
hyp: HERE AGAIN
{'N': 3, 'C': 1, 'W': 2, 'I': 0, 'D': 1, 'S': 1}
ref: HERE WE GO
hyp: HERE WE GET
{'N': 3, 'C': 2, 'W': 1, 'I': 0, 'D': 0, 'S': 1}
HERE WE GO
key: AMI_ES2011a_H00_FEE041_0003714_0003915
ref: WELCOME EVERYBODY
hyp: WELCOME EVERYBODY
{'N': 2, 'C': 2, 'W': 0, 'I': 0, 'D': 0, 'S': 0}
ref: WELCOME EVERYBODY
hyp: WELCOME TO EVERYBODY
{'N': 2, 'C': 2, 'W': 1, 'I': 1, 'D': 0, 'S': 0}
ref: WELCOME EVERYBODY
hyp: WELL COME EVERYBODY
{'N': 2, 'C': 1, 'W': 2, 'I': 1, 'D': 0, 'S': 1}
ref: WELCOME EVERYBODY
hyp: WELCOME AT EVERYBODY
{'N': 2, 'C': 2, 'W': 1, 'I': 1, 'D': 0, 'S': 0}
ref: WELCOME EVERYBODY
hyp: WELLCOME EVERYBODY
{'N': 2, 'C': 1, 'W': 1, 'I': 0, 'D': 0, 'S': 1}
ref: WELCOME EVERYBODY
hyp: WELCOME EVERYONE READY
{'N': 2, 'C': 1, 'W': 2, 'I': 1, 'D': 0, 'S': 1}
WELCOME EVERYBODY
key: AMI_ES2011a_H00_FEE041_0003915_0004332
ref: UM I'M

ref: UM WE'RE GONNA DO SOME TOOL TRAINING PROJECT PLAN AND DISCUSS
hyp: UM WERE GONNA DO SOME TOOL TRAINING PROJECT PLAN AND DISCUSSED
{'N': 11, 'C': 9, 'W': 2, 'I': 0, 'D': 0, 'S': 2}
ref: UM WE'RE GONNA DO SOME TOOL TRAINING PROJECT PLAN AND DISCUSS
hyp: I'M WE'RE GONNA DO SOME TOOL TRAINING PROJECT PLAN AND DISCUSSED
{'N': 11, 'C': 9, 'W': 2, 'I': 0, 'D': 0, 'S': 2}
ref: UM WE'RE GONNA DO SOME TOOL TRAINING PROJECT PLAN AND DISCUSS
hyp: UM WERE GONNA DO SOME TOOL TRAINING PROJECT PLAN AN DISCUSS
{'N': 11, 'C': 9, 'W': 2, 'I': 0, 'D': 0, 'S': 2}
ref: UM WE'RE GONNA DO SOME TOOL TRAINING PROJECT PLAN AND DISCUSS
hyp: I'M WE'RE GONNA DO SOME TOOL TRAINING PROJECT PLAN AN DISCUSS
{'N': 11, 'C': 9, 'W': 2, 'I': 0, 'D': 0, 'S': 2}
ref: UM WE'RE GONNA DO SOME TOOL TRAINING PROJECT PLAN AND DISCUSS
hyp: UM WERE GONNA DO SOME TOOL TRAINING PROJECT PLAN UM DISCUSS
{'N': 11, 'C': 9, 'W': 2, 'I': 0, 'D': 0, 'S': 2}
ref: UM WE'RE GONNA DO SOME TOOL TRAINING PROJECT PLAN AND DISCUSS
hyp: I'M WE'R

ref: SO THROUGHOUT OUR NEXT COUPLE OF MEETINGS WE'LL WE'LL BE COVERING THESE THINGS
hyp: SO THROUGHOUT OR NEXT COUPLE OF MEETINGS WERE WILL BE COVERING THESE THINGS
{'N': 13, 'C': 10, 'W': 3, 'I': 0, 'D': 0, 'S': 3}
ref: SO THROUGHOUT OUR NEXT COUPLE OF MEETINGS WE'LL WE'LL BE COVERING THESE THINGS
hyp: SO THROW OUT OR NEXT COUPLE OF MEETINGS WE'LL WE'LL BE COVERING THESE THINGS
{'N': 13, 'C': 11, 'W': 3, 'I': 1, 'D': 0, 'S': 2}
ref: SO THROUGHOUT OUR NEXT COUPLE OF MEETINGS WE'LL WE'LL BE COVERING THESE THINGS
hyp: SO THROUGHOUT OUR NEXT COUPLE OF MEETINGS WE'LL WE'LL BE COVERING IN THESE THINGS
{'N': 13, 'C': 13, 'W': 1, 'I': 1, 'D': 0, 'S': 0}
ref: SO THROUGHOUT OUR NEXT COUPLE OF MEETINGS WE'LL WE'LL BE COVERING THESE THINGS
hyp: SO THROUGHOUT ARE NEXT COUPLE OF MEETINGS WILL WILL BE COVERING THESE THINGS
{'N': 13, 'C': 10, 'W': 3, 'I': 0, 'D': 0, 'S': 3}
ref: SO THROUGHOUT OUR NEXT COUPLE OF MEETINGS WE'LL WE'LL BE COVERING THESE THINGS
hyp: SO THROUGHOUT OUR NEXT COUPLE OF MEETIN

ref: THEY'RE GRACEFUL
hyp: MY GRACEFUL
{'N': 2, 'C': 1, 'W': 1, 'I': 0, 'D': 0, 'S': 1}
ref: THEY'RE GRACEFUL
hyp: THEY'D GRACEFUL
{'N': 2, 'C': 1, 'W': 1, 'I': 0, 'D': 0, 'S': 1}
ref: THEY'RE GRACEFUL
hyp: HEY GRACEFUL
{'N': 2, 'C': 1, 'W': 1, 'I': 0, 'D': 0, 'S': 1}
ref: THEY'RE GRACEFUL
hyp: LIKE GRACEFUL
{'N': 2, 'C': 1, 'W': 1, 'I': 0, 'D': 0, 'S': 1}
ref: THEY'RE GRACEFUL
hyp: YE GRACEFUL
{'N': 2, 'C': 1, 'W': 1, 'I': 0, 'D': 0, 'S': 1}
THEY'RE GRACEFUL
key: AMI_ES2011a_H00_FEE041_0030285_0030548
ref: SLEEK
hyp: SLEEK
{'N': 1, 'C': 1, 'W': 0, 'I': 0, 'D': 0, 'S': 0}
ref: SLEEK
hyp: SLEEP
{'N': 1, 'C': 0, 'W': 1, 'I': 0, 'D': 0, 'S': 1}
ref: SLEEK
hyp: SLEEK AND
{'N': 1, 'C': 1, 'W': 1, 'I': 1, 'D': 0, 'S': 0}
SLEEK
key: AMI_ES2011a_H00_FEE041_0030922_0031388
ref: I DON'T KNOW HOW INTELLIGENT THAT ONE LOOKS
hyp: AND THEN THERE HOW INTELLIGENT THAT ONE LOOKS
{'N': 8, 'C': 5, 'W': 3, 'I': 0, 'D': 0, 'S': 3}
ref: I DON'T KNOW HOW INTELLIGENT THAT ONE LOOKS
hyp: AND THEN THEY'RE HOW I

ref: WATER RESISTANT STRONG AND FURRY
hyp: WATER RESISTANT STRONG AND VERY
{'N': 5, 'C': 4, 'W': 1, 'I': 0, 'D': 0, 'S': 1}
ref: WATER RESISTANT STRONG AND FURRY
hyp: WATER RESISTANT STRONG AND FURTHER
{'N': 5, 'C': 4, 'W': 1, 'I': 0, 'D': 0, 'S': 1}
ref: WATER RESISTANT STRONG AND FURRY
hyp: WATER RESISTANT STRONG AND FOR THREE
{'N': 5, 'C': 4, 'W': 2, 'I': 1, 'D': 0, 'S': 1}
ref: WATER RESISTANT STRONG AND FURRY
hyp: WATER RESISTANT STRONG AND FURNITURE
{'N': 5, 'C': 4, 'W': 1, 'I': 0, 'D': 0, 'S': 1}
ref: WATER RESISTANT STRONG AND FURRY
hyp: WALTER RESISTANT STRONG AND THREE
{'N': 5, 'C': 3, 'W': 2, 'I': 0, 'D': 0, 'S': 2}
ref: WATER RESISTANT STRONG AND FURRY
hyp: WATER RESISTANT STRONG AND FERRY
{'N': 5, 'C': 4, 'W': 1, 'I': 0, 'D': 0, 'S': 1}
ref: WATER RESISTANT STRONG AND FURRY
hyp: WHAT I RESISTANT STRONG AND FURRY
{'N': 5, 'C': 4, 'W': 2, 'I': 1, 'D': 0, 'S': 1}
WATER RESISTANT STRONG AND FURRY
key: AMI_ES2011a_H00_FEE041_0049873_0050234
ref: WHAT DO YOU THINK YEAH
hyp: WE T

...

key: AMI_IB4001_H00_MIO092_0027238_0027277
ref: MM-HMM
hyp: MM
{'N': 1, 'C': 0, 'W': 1, 'I': 0, 'D': 0, 'S': 1}
ref: MM-HMM
hyp: HMM
{'N': 1, 'C': 0, 'W': 1, 'I': 0, 'D': 0, 'S': 1}
ref: MM-HMM
hyp: MM-HMM
{'N': 1, 'C': 1, 'W': 0, 'I': 0, 'D': 0, 'S': 0}
ref: MM-HMM
hyp: MM MM
{'N': 1, 'C': 0, 'W': 2, 'I': 1, 'D': 0, 'S': 1}
MM-HMM
key: AMI_IB4001_H00_MIO092_0028824_0028862
ref: MM
hyp: MM
{'N': 1, 'C': 1, 'W': 0, 'I': 0, 'D': 0, 'S': 0}
ref: MM
hyp: HMM
{'N': 1, 'C': 0, 'W': 1, 'I': 0, 'D': 0, 'S': 1}
ref: MM
hyp: MM-HMM
{'N': 1, 'C': 0, 'W': 1, 'I': 0, 'D': 0, 'S': 1}
ref: MM
hyp: MM MM
{'N': 1, 'C': 1, 'W': 1, 'I': 1, 'D': 0, 'S': 0}
MM
key: AMI_IB4001_H00_MIO092_0029120_0029164
ref: YEAH
hyp: YEAH
{'N': 1, 'C': 1, 'W': 0, 'I': 0, 'D': 0, 'S': 0}
YEAH
key: AMI_IB4001_H00_MIO092_0029433_0029548
ref: MM YEAH
hyp: MM YEAH
{'N': 2, 'C': 2, 'W': 0, 'I': 0, 'D': 0, 'S': 0}
ref: MM YEAH
hyp: HMM YEAH
{'N': 2, 'C': 1, 'W': 1, 'I': 0, 'D': 0, 'S': 1}
ref: MM YEAH
hyp: MM-HMM YEAH
{'N': 2, 'C

ref: I MEAN IT'S COMPLETELY DIFFERENT WORK SO WE CAN DEAL WITH ADMINISTRATION AND DECIDE SOMETHING FOR ADMINISTRATION AND THEN
hyp: I MEAN IT'S COMPLETELY DIFFERENT WORK SO WE CAN DEAL WITH ADMINISTRATION AND DECIDE SOMETHING FARM ADMINISTRATION AND THEN
{'N': 19, 'C': 18, 'W': 1, 'I': 0, 'D': 0, 'S': 1}
I MEAN IT'S COMPLETELY DIFFERENT WORK SO WE CAN DEAL WITH ADMINISTRATION AND DECIDE SOMETHING FOR ADMINISTRATION AND THEN
key: AMI_IB4001_H00_MIO092_0037713_0037769
ref: FOR THE OTHER
hyp: FOR THE OTHER
{'N': 3, 'C': 3, 'W': 0, 'I': 0, 'D': 0, 'S': 0}
ref: FOR THE OTHER
hyp: FOR THE OTHERS
{'N': 3, 'C': 2, 'W': 1, 'I': 0, 'D': 0, 'S': 1}
ref: FOR THE OTHER
hyp: SO THE OTHER
{'N': 3, 'C': 2, 'W': 1, 'I': 0, 'D': 0, 'S': 1}
ref: FOR THE OTHER
hyp: FOR THE OTHER UH
{'N': 3, 'C': 3, 'W': 1, 'I': 1, 'D': 0, 'S': 0}
ref: FOR THE OTHER
hyp: OR THE OTHER
{'N': 3, 'C': 2, 'W': 1, 'I': 0, 'D': 0, 'S': 1}
ref: FOR THE OTHER
hyp: FOR THE EITHER
{'N': 3, 'C': 2, 'W': 1, 'I': 0, 'D': 0, 'S': 1}
ref:

ref: SO YOU WON'T SHARE AN OFFICE WITH GISELLA UNLESS YOU ARE FIFTY PER CENT AND NOT THE FIFTY PER CENT GISELLA IS WORKING WHICH IS ANOTHER CONDITION
hyp: SO YOU WON'T SELL AN OFFICE WITH <unk> UNLESS YOU HAVE FIFTY PERCENT AND NOT THE FIFTY PERCENT <unk> WORKING WHICH IS ANOTHER CONDITION
{'N': 27, 'C': 18, 'W': 9, 'I': 0, 'D': 3, 'S': 6}
ref: SO YOU WON'T SHARE AN OFFICE WITH GISELLA UNLESS YOU ARE FIFTY PER CENT AND NOT THE FIFTY PER CENT GISELLA IS WORKING WHICH IS ANOTHER CONDITION
hyp: SO YOU WON'T SAY AN OFFICE WITH <unk> UNLESS YOU HAVE FIFTY PERCENT AND NOT THE FIFTY PERCENT <unk> WORKING WHICH IS ANOTHER CONDITION
{'N': 27, 'C': 18, 'W': 9, 'I': 0, 'D': 3, 'S': 6}
ref: SO YOU WON'T SHARE AN OFFICE WITH GISELLA UNLESS YOU ARE FIFTY PER CENT AND NOT THE FIFTY PER CENT GISELLA IS WORKING WHICH IS ANOTHER CONDITION
hyp: SO YOU WANNA SAY AN OFFICE WITH <unk> UNLESS YOU HAVE FIFTY PERCENT AND NOT THE FIFTY PERCENT <unk> WORKING WHICH IS ANOTHER CONDITION
{'N': 27, 'C': 17, 'W': 10,

ref: SO I DON'T KNOW MAYBE WE CAN DECIDE THAT GISELLA IS HAVING ONE OF THE ONE PERSON ROOM
hyp: TO I DON'T KNOW MAYBE WE CAN DECIDE THAT IS ALLIES HAVING ONE OF THE ONE PERSON ROOM
{'N': 18, 'C': 15, 'W': 3, 'I': 0, 'D': 0, 'S': 3}
ref: SO I DON'T KNOW MAYBE WE CAN DECIDE THAT GISELLA IS HAVING ONE OF THE ONE PERSON ROOM
hyp: TOO I DON'T KNOW MAYBE WE CAN DECIDE <unk> HAVING ONE OF THE ONE PERSON ROOM
{'N': 18, 'C': 14, 'W': 4, 'I': 0, 'D': 2, 'S': 2}
ref: SO I DON'T KNOW MAYBE WE CAN DECIDE THAT GISELLA IS HAVING ONE OF THE ONE PERSON ROOM
hyp: TWO I DON'T KNOW MAYBE WE CAN DECIDE THAT DOES ALLIES HAVING ONE OF THE ONE PERSON ROOM
{'N': 18, 'C': 15, 'W': 3, 'I': 0, 'D': 0, 'S': 3}
ref: SO I DON'T KNOW MAYBE WE CAN DECIDE THAT GISELLA IS HAVING ONE OF THE ONE PERSON ROOM
hyp: TO I DON'T KNOW MAYBE WE CAN DECIDE THAT DOES ALLIES HAVING ONE OF THE ONE PERSON ROOM
{'N': 18, 'C': 15, 'W': 3, 'I': 0, 'D': 0, 'S': 3}
ref: SO I DON'T KNOW MAYBE WE CAN DECIDE THAT GISELLA IS HAVING ONE OF THE 

KeyboardInterrupt: 